In [ ]:
# -*- coding: utf-8 -*-
import threading, random, time

# Обедающие философы
# 5 мудрецов и 5 палочек для лапши(или вилочек). Для еды нужно ухватить две палочки.
#
# Для устранения блокировки (Deadlock) используется механизм мьютексов (lock).
# Procedure is to do block while waiting to get first fork, and a nonblocking
# acquire of second fork.  If failed to get second fork, release first fork,
# swap which fork is first and which is second and retry until getting both.

class Filosoff(threading.Thread):

    running = True

    def __init__(self, xname, forkOne, forkTwo):
        #threading.Thread.__init__(self)
        super().__init__()
        self.name = xname
        self.forkOnLeft = forkOne
        self.forkOnRight = forkTwo
        self.f_eat_count =0 

    def run(self):
        while self.running:
            #  Мудрец думает (на самом деле спит)
            time.sleep(random.uniform(2,5))
            print (self.name, 'голодный.')
            self.dine()
        else:
            print (self.name,' поел ', self.f_eat_count," раз" )
            return

    def dine(self):
        fork1, fork2 = self.forkOnLeft, self.forkOnRight

        while self.running:
            fork1.acquire(True)
			# простой вариант контроллера__!__#
            #fork2.acquire(True)
            #break
            # анти-дедлок -vvvv- (deadlock prevent section)
            locked = fork2.acquire(False)
            if locked: break
            fork1.release()
            # анти-дедлок -^^^^-
            # улучшим эффективность захвата -vvvv-
            print (self.name, 'поменял порядок захвата.')
            fork1, fork2 = fork2, fork1
            # попробуем начать с другого ресурса -^^^^-
        else:
            return
        self.f_eat_count += 1
        print (self.name, 'начал есть.')
        time.sleep(random.uniform(3,6))
        print (self.name, 'наелся и думает.')
        fork1.release()
        fork2.release()

In [ ]:
def DiningFilosofs(numfilos):
    if (numfilos < 2) or (numfilos > 11) :
       print('Число философов от 2 до 11!')
       return

    # создание семафоров ресурсов (forks) в виде мьютексов
    forks = [threading.Lock() for n in range(numfilos)]

    philosopherNames = ('1:Кант:','2:Маркс:','3:Платон:','4:Руссо:','5:Сократ:',
                        '6:Пифагор:','7:Гегель:','8:Вольтер:','9:Декарт:',
                        '10:ЛаоЦзы:','11:Рассел:','12:Будда:')
    
    # список имен по-английски (а вдруг пригодится?)
    # philosopherNames = ('1:Kant:','2:Marx:','3:Plato:','4:Russo:','5:Sockrat:',
    #                    '6:Pifagor:','7:Gheghel:','8:Voltair:','9:Dekart:',
    #                    '10:Lao:','11:Russel:')

    philosophers = [Filosoff(philosopherNames[i], forks[i%numfilos],
                                forks[(i+1)%numfilos]) for i in range(numfilos)]

    random.seed(1537)
    modelstart=time.perf_counter_ns()
    Filosoff.running = True
    for p in philosophers: p.start()
    time.sleep(40)
    Filosoff.running = False
    # Ожидание завершения потоков
    for p in philosophers: p.join()
    modelfini=time.perf_counter_ns()
    print ("== Все закончили! Время =", (modelfini-modelstart)/1000000, "msec")

In [ ]:
DiningFilosofs(10)

Вариант с ограничением еды

In [ ]:
# -*- coding: utf-8 -*-
import threading, random, time

# Обедающие философы
# 5 мудрецов и 5 палочек для суши(или вилочек). Для еды нужно ухватить две палочки.
# Для устранения блокировки (Deadlock) используется механизм мьютексов (lock).

class Filosofa(threading.Thread):
    #running = True

    def __init__(self, xname, forkOne, forkTwo):
        super().__init__()
        self.name = xname
        self.forkOnLeft = forkOne
        self.forkOnRight = forkTwo
        self.sushi_eaten =0 

    def run(self) -> None:
        global sushi
        while sushi > 0:
            #  Мудрец думает
            time.sleep(random.normalvariate(4,1))
            print (self.name, 'голодный.')
            # простой вариант !__#
            self.forkOnLeft.acquire(True)
            self.forkOnRight.acquire(True)
            # можно поесть
            if sushi > 0:
               sushi -= 1
               self.sushi_eaten += 1
               print (self.name, 'начал есть.')
            time.sleep(random.expovariate(1/3.0))
            print (self.name, 'наелся и думает.')
            self.forkOnLeft.release()
            self.forkOnRight.release()
        else:
            print (self.name,' поел ', self.sushi_eaten," раз" )
            return
        

In [ ]:
def DiningFilosofas(numfilos):
    if (numfilos < 2) or (numfilos > 11) :
       print('Число философов от 2 до 11!')
       return
    
    # создание семафоров ресурсов (палочек) в виде мьютексов
    forks = [threading.Lock() for n in range(numfilos)]

    philosophNames = ('1:Кант:','2:Маркс:','3:Платон:','4:Руссо:','5:Сократ:',
                        '6:Пифагор:','7:Гегель:','8:Вольтер:','9:Декарт:',
                        '10:ЛаоЦзы:','11:Рассел:','12:Будда:')

    philosofs = [Filosofa(philosophNames[i], forks[i%numfilos],
                           forks[(i+1)%numfilos]) for i in range(numfilos)]

    random.seed(1537)
    modelstart=time.perf_counter_ns()
    for p in philosofs: p.start()
    #time.sleep(40)
    # Ожидание завершения потоков
    for p in philosofs: p.join()
    modelfini=time.perf_counter_ns()
    print ("== Все закончили! Время =", (modelfini-modelstart)/1000000, "msec")

In [ ]:
sushi=50
DiningFilosofas(10)

Вариант с официантом

In [ ]:
# -*- coding: utf-8 -*-
import threading, random, time

# Обедающие философы
# 5 мудрецов и 5 палочек для суши(или вилочек). Для еды нужно ухватить две палочки.
# Для устранения блокировки (Deadlock) используется механизм мьютексов (lock).

class Oficiant:
    def __init__(self) -> None:
        self.mutex = threading.Lock()

    def ask_for_forks(self, left_fork, right_fork) -> None:
        with self.mutex:
            left_fork.acquire()
            print("+левую вилку взял")
            right_fork.acquire()
            print("+правую вилку взял\n")

    def release_forks(self, left_fork, right_fork) -> None:
        right_fork.release()
        print("-правую вилку положил")
        left_fork.release()
        print("-левую вилку положил\n")


class Filosofik(threading.Thread):
    #running = True

    def __init__(self, xname, forkOne, forkTwo, waiter: Oficiant):
        super().__init__()
        self.name = xname
        self.forkOnLeft = forkOne
        self.forkOnRight = forkTwo
        self.sushi_eaten =0
        self.waiter = waiter

    def run(self) -> None:
        global sushi
        while sushi > 0:
            #  Мудрец думает
            time.sleep(random.normalvariate(4,1))
            print (self.name, 'голодный.')
            print(f"{self.name} запросил официанта")
            self.waiter.ask_for_forks(self.forkOnLeft, self.forkOnRight)
            # можно поесть
            if sushi > 0:
               sushi -= 1
               self.sushi_eaten += 1
               print (self.name, 'начал есть.')
            time.sleep(random.expovariate(1/3.0))
            print(f"{self.name} отдал официанту")
            self.waiter.release_forks(self.forkOnLeft, self.forkOnRight)
            print (self.name, 'наелся и думает.')
        else:
            print (self.name,' поел ', self.sushi_eaten," раз" )
            return
        

In [ ]:
def DiningFilosofik(numfilos):
    if (numfilos < 2) or (numfilos > 11) :
       print('Число философов от 2 до 11!')
       return
    
    # создание семафоров ресурсов (палочек) в виде мьютексов
    forks = [threading.Lock() for n in range(numfilos)]

    philosophNames = ('1:Кант:','2:Маркс:','3:Платон:','4:Руссо:','5:Сократ:',
                        '6:Пифагор:','7:Гегель:','8:Вольтер:','9:Декарт:',
                        '10:ЛаоЦзы:','11:Рассел:','12:Будда:')
    waiter = Oficiant()
    philosofs = [Filosofik(philosophNames[i], forks[i%numfilos],
                           forks[(i+1)%numfilos], waiter) for i in range(numfilos)]
    random.seed(1537)
    modelstart=time.perf_counter_ns()
    for p in philosofs: p.start()
    # Ожидание завершения потоков
    for p in philosofs: p.join()
    modelfini=time.perf_counter_ns()
    print ("== Все закончили! Время =", (modelfini-modelstart)/1000000, "msec")

In [ ]:
sushi=50
DiningFilosofik(10)